Resources Used
- wget.download('https://tensorflow-object-detection-api-tutorial.readthedocs.io/en/latest/_downloads/da4babe668a8afb093cc7776d7e630f3/generate_tfrecord.py')
- Setup https://tensorflow-object-detection-api-tutorial.readthedocs.io/en/latest/install.html

# 0. Setup Paths

In [2]:
# run
WORKSPACE_PATH = 'Tensorflow/workspace'
SCRIPTS_PATH = 'Tensorflow/scripts'
APIMODEL_PATH = 'Tensorflow/models'
ANNOTATION_PATH = WORKSPACE_PATH+'/annotations'
IMAGE_PATH = WORKSPACE_PATH+'/images'
MODEL_PATH = WORKSPACE_PATH+'/models'
PRETRAINED_MODEL_PATH = WORKSPACE_PATH+'/pre-trained-models'
CONFIG_PATH = MODEL_PATH+'/my_ssd_mobnet/pipeline.config'
CHECKPOINT_PATH = MODEL_PATH+'/my_ssd_mobnet/'

# 5. Update Config For Transfer Learning

In [3]:
# run
import tensorflow as tf
from object_detection.utils import config_util
from object_detection.protos import pipeline_pb2
from google.protobuf import text_format

# 7. Load Train Model From Checkpoint

In [4]:
# run
import os
import tensorflow as tf
from object_detection.utils import label_map_util
from object_detection.utils import visualization_utils as viz_utils
from object_detection.builders import model_builder

In [5]:
# run
# Load pipeline config and build a detection model
configs = config_util.get_configs_from_pipeline_file(CONFIG_PATH)
detection_model = model_builder.build(model_config=configs['model'], is_training=False)

# Restore checkpoint
ckpt = tf.compat.v2.train.Checkpoint(model=detection_model)
ckpt.restore(os.path.join(CHECKPOINT_PATH, 'ckpt-6')).expect_partial()

@tf.function
def detect_fn(image):
    image, shapes = detection_model.preprocess(image)
    prediction_dict = detection_model.predict(image, shapes)
    detections = detection_model.postprocess(prediction_dict, shapes)
    return detections


# 8. Detect in Real-Time

In [6]:
# run
import cv2 
import numpy as np

In [7]:
# run
category_index = label_map_util.create_category_index_from_labelmap(ANNOTATION_PATH+'/label_map.pbtxt')

In [8]:
# run
# Setup capture
cap = cv2.VideoCapture(0)
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

In [9]:
# run
while True: 
    ret, frame = cap.read()
    image_np = np.array(frame)
    
    input_tensor = tf.convert_to_tensor(np.expand_dims(image_np, 0), dtype=tf.float32)
    detections = detect_fn(input_tensor)
    
    num_detections = int(detections.pop('num_detections'))
    detections = {key: value[0, :num_detections].numpy()
                  for key, value in detections.items()}
    detections['num_detections'] = num_detections

    # detection_classes should be ints.
    detections['detection_classes'] = detections['detection_classes'].astype(np.int64)
    
    pred = get_prediction(input_tensor)
    print(pred)

    label_id_offset = 1
    image_np_with_detections = image_np.copy()

    viz_utils.visualize_boxes_and_labels_on_image_array(
                image_np_with_detections,
                detections['detection_boxes'],
                detections['detection_classes']+label_id_offset,
                detections['detection_scores'],
                category_index,
                use_normalized_coordinates=True,
                max_boxes_to_draw=5,
                min_score_thresh=.5,
                agnostic_mode=False)

    cv2.imshow('object detection',  cv2.resize(image_np_with_detections, (800, 600)))
    
    if cv2.waitKey(1) & 0xFF == ord('q'):
        cap.release()
        break

{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 5.2156878e-01,  5.2156878e-01,  5.2156878e-01],
         [ 5.2941191e-01,  5.2941191e-01,  5.2941191e-01],
         [ 5.5294132e-01,  5.5294132e-01,  5.5294132e-01],
         ...,
         [-3.5686272e-01, -2.3921561e-01, -1.9215679e-01],
         [-3.4901959e-01, -2.4705875e-01, -2.3921561e-01],
         [-3.8039213e-01, -2.8627449e-01, -3.0196077e-01]],

        [[ 5.2156878e-01,  5.2156878e-01,  5.2156878e-01],
         [ 5.2941191e-01,  5.2941191e-01,  5.2941191e-01],
         [ 5.4901975e-01,  5.4901975e-01,  5.4901975e-01],
         ...,
         [-3.3333331e-01, -2.5490192e-01, -1.7254895e-01],
         [-3.4117645e-01, -2.7843136e-01, -2.3529404e-01],
         [-3.7647057e-01, -3.2549018e-01, -3.0588233e-01]],

        [[ 5.2156878e-01,  5.2156878e-01,  5.2156878e-01],
         [ 5.2941191e-01,  5.2941191e-01,  5.2941191e-01],
         [ 5.4509819e-01,  5.4509819e-01,  5.4509819e-01],
 

{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 0.47450984,  0.427451  ,  0.41960788],
         [ 0.4666667 ,  0.43529415,  0.427451  ],
         [ 0.48235297,  0.45098042,  0.43529415],
         ...,
         [-0.3490196 , -0.35686272, -0.3333333 ],
         [-0.34117645, -0.34117645, -0.34117645],
         [-0.372549  , -0.38039213, -0.38039213]],

        [[ 0.4666667 ,  0.43137258,  0.41960788],
         [ 0.4666667 ,  0.43529415,  0.43137258],
         [ 0.48235297,  0.45098042,  0.44705886],
         ...,
         [-0.3490196 , -0.35686272, -0.33725488],
         [-0.35294116, -0.35294116, -0.3490196 ],
         [-0.36862743, -0.3843137 , -0.37647057]],

        [[ 0.45882356,  0.43529415,  0.427451  ],
         [ 0.4666667 ,  0.427451  ,  0.43529415],
         [ 0.4666667 ,  0.43529415,  0.4431373 ],
         ...,
         [-0.3490196 , -0.35686272, -0.3333333 ],
         [-0.35686272, -0.36470586, -0.34117645],
         [-0.372549  ,

{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 0.47450984,  0.41960788,  0.427451  ],
         [ 0.45882356,  0.41960788,  0.427451  ],
         [ 0.45882356,  0.4431373 ,  0.4431373 ],
         ...,
         [-0.38039213, -0.31764704, -0.27058822],
         [-0.35686272, -0.32549018, -0.20784307],
         [-0.41176468, -0.42745095, -0.24705875]],

        [[ 0.45098042,  0.40784317,  0.4156863 ],
         [ 0.454902  ,  0.4156863 ,  0.42352945],
         [ 0.4666667 ,  0.4431373 ,  0.4431373 ],
         ...,
         [-0.3843137 , -0.34509802, -0.27843136],
         [-0.36470586, -0.3490196 , -0.23921564],
         [-0.3960784 , -0.41960782, -0.27058822]],

        [[ 0.43529415,  0.4039216 ,  0.41176474],
         [ 0.45098042,  0.41960788,  0.427451  ],
         [ 0.45882356,  0.4431373 ,  0.4431373 ],
         ...,
         [-0.38039213, -0.38039213, -0.27843136],
         [-0.36470586, -0.36470586, -0.27843136],
         [-0.35686272,

{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 0.427451  ,  0.427451  ,  0.427451  ],
         [ 0.4431373 ,  0.4431373 ,  0.4431373 ],
         [ 0.45882356,  0.45098042,  0.45098042],
         ...,
         [-0.38823527, -0.36470586, -0.30196077],
         [-0.38039213, -0.3960784 , -0.34117645],
         [-0.34117645, -0.40392154, -0.3490196 ]],

        [[ 0.43137258,  0.43137258,  0.43137258],
         [ 0.4431373 ,  0.4431373 ,  0.4431373 ],
         [ 0.454902  ,  0.44705886,  0.44705886],
         ...,
         [-0.40392154, -0.38039213, -0.31764704],
         [-0.37647057, -0.39215684, -0.3333333 ],
         [-0.34117645, -0.39215684, -0.32941175]],

        [[ 0.43529415,  0.43529415,  0.43529415],
         [ 0.4431373 ,  0.4431373 ,  0.4431373 ],
         [ 0.4431373 ,  0.43529415,  0.43529415],
         ...,
         [-0.36470586, -0.3490196 , -0.29411763],
         [-0.38823527, -0.3960784 , -0.32549018],
         [-0.36470586,

{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 0.45098042,  0.4431373 ,  0.41176474],
         [ 0.45098042,  0.4431373 ,  0.41176474],
         [ 0.45882356,  0.45098042,  0.427451  ],
         ...,
         [-0.372549  , -0.3490196 , -0.31764704],
         [-0.372549  , -0.372549  , -0.32549018],
         [-0.35686272, -0.35686272, -0.29411763]],

        [[ 0.43529415,  0.427451  ,  0.40000004],
         [ 0.43921572,  0.43137258,  0.4039216 ],
         [ 0.45098042,  0.43921572,  0.41960788],
         ...,
         [-0.372549  , -0.3490196 , -0.32941175],
         [-0.38823527, -0.38039213, -0.35294116],
         [-0.37647057, -0.372549  , -0.32941175]],

        [[ 0.427451  ,  0.41176474,  0.4039216 ],
         [ 0.43529415,  0.41960788,  0.41176474],
         [ 0.45098042,  0.43529415,  0.427451  ],
         ...,
         [-0.36470586, -0.3490196 , -0.3490196 ],
         [-0.38823527, -0.38039213, -0.38039213],
         [-0.38039213,

...

{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 0.39607847,  0.4039216 ,  0.38823533],
         [ 0.41960788,  0.427451  ,  0.41176474],
         [ 0.43529415,  0.4431373 ,  0.41960788],
         ...,
         [-0.3960784 , -0.36470586, -0.38039213],
         [-0.3490196 , -0.3490196 , -0.372549  ],
         [-0.35686272, -0.38039213, -0.38039213]],

        [[ 0.4039216 ,  0.41176474,  0.3921569 ],
         [ 0.41176474,  0.4156863 ,  0.40784317],
         [ 0.43137258,  0.43529415,  0.427451  ],
         ...,
         [-0.36862743, -0.34117645, -0.34117645],
         [-0.34117645, -0.34509802, -0.34509802],
         [-0.372549  , -0.39999998, -0.38823527]],

        [[ 0.4039216 ,  0.41176474,  0.39607847],
         [ 0.4039216 ,  0.4039216 ,  0.4039216 ],
         [ 0.41176474,  0.41176474,  0.41176474],
         ...,
         [-0.3960784 , -0.372549  , -0.35686272],
         [-0.3960784 , -0.3960784 , -0.372549  ],
         [-0.38039213,

         -5.288826 ]]], dtype=float32)>}
{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 0.39607847,  0.39607847,  0.39607847],
         [ 0.3803922 ,  0.39607847,  0.39607847],
         [ 0.41960788,  0.43529415,  0.43529415],
         ...,
         [-0.38823527, -0.372549  , -0.372549  ],
         [-0.3333333 , -0.32549018, -0.32549018],
         [-0.4352941 , -0.4352941 , -0.42745095]],

        [[ 0.41176474,  0.40784317,  0.40784317],
         [ 0.40784317,  0.40784317,  0.40784317],
         [ 0.43137258,  0.43529415,  0.43529415],
         ...,
         [-0.38039213, -0.38039213, -0.372549  ],
         [-0.3333333 , -0.34509802, -0.33725488],
         [-0.37647057, -0.40392154, -0.38039213]],

        [[ 0.41960788,  0.4039216 ,  0.4039216 ],
         [ 0.427451  ,  0.4039216 ,  0.4039216 ],
         [ 0.427451  ,  0.41960788,  0.41960788],
         ...,
         [-0.34117645, -0.36470586, -0.34117645],
         [-0.31764704, -0.36470

{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 0.39607847,  0.38823533,  0.35686278],
         [ 0.427451  ,  0.41960788,  0.39607847],
         [ 0.4431373 ,  0.427451  ,  0.41960788],
         ...,
         [-0.3098039 , -0.34117645, -0.2156862 ],
         [-0.38039213, -0.38823527, -0.2862745 ],
         [-0.41960782, -0.41176468, -0.32549018]],

        [[ 0.42352945,  0.41176474,  0.38823533],
         [ 0.43529415,  0.42352945,  0.40784317],
         [ 0.427451  ,  0.4156863 ,  0.39607847],
         ...,
         [-0.35294116, -0.372549  , -0.26666662],
         [-0.38823527, -0.3960784 , -0.30588233],
         [-0.3843137 , -0.3843137 , -0.31372547]],

        [[ 0.39607847,  0.38823533,  0.3803922 ],
         [ 0.41176474,  0.4039216 ,  0.39607847],
         [ 0.4431373 ,  0.427451  ,  0.41960788],
         ...,
         [-0.36470586, -0.372549  , -0.30196077],
         [-0.38039213, -0.38823527, -0.3333333 ],
         [-0.40392154,

{'preprocessed_inputs': <tf.Tensor: shape=(1, 320, 320, 3), dtype=float32, numpy=
array([[[[ 0.41960788,  0.41176474,  0.43529415],
         [ 0.41960788,  0.41960788,  0.41960788],
         [ 0.427451  ,  0.427451  ,  0.427451  ],
         ...,
         [-0.41176468, -0.45098037, -0.34117645],
         [-0.38823527, -0.4352941 , -0.29411763],
         [-0.3960784 , -0.45098037, -0.2862745 ]],

        [[ 0.41176474,  0.40784317,  0.4156863 ],
         [ 0.4156863 ,  0.4156863 ,  0.4156863 ],
         [ 0.42352945,  0.42352945,  0.42352945],
         ...,
         [-0.38039213, -0.41568625, -0.3098039 ],
         [-0.3607843 , -0.40392154, -0.27843136],
         [-0.4078431 , -0.4588235 , -0.3098039 ]],

        [[ 0.41176474,  0.41176474,  0.41176474],
         [ 0.41176474,  0.41176474,  0.41176474],
         [ 0.41176474,  0.41176474,  0.41176474],
         ...,
         [-0.36470586, -0.3960784 , -0.3098039 ],
         [-0.3490196 , -0.38039213, -0.27843136],
         [-0.3960784 ,

KeyboardInterrupt: 

In [ ]:
detections = detect_fn(input_tensor)

In [ ]:
from matplotlib import pyplot as plt